In [1]:
# !pip install geojson
# !pip install folium
# !pip install geopandas
# !pip install pyogrio

import pandas as pd
import numpy as np
import geopandas as gpd
import folium
import geopandas as gpd

In [ ]:
# Paramètres externes
# ratio_ev_baule = 0.046 # 4.6% 
ratio_ev = 0.03 
conso_kwh_km = 0.2

# Mobilité pendulaire

In [3]:
file = '../data/RP2020_MOBPRO_csv/FD_MOBPRO_2020.csv'
df_mob_full = pd.read_csv(file, sep=';')
len(df_mob_full)

C:\Users\eliot\AppData\Local\Temp\ipykernel_3640\443605898.py:2: DtypeWarning: Columns (0,1,2,3,13,14,15,17,21,23,26,29,30,31) have mixed types. Specify dtype option on import or set low_memory=False.
  df_mob_full = pd.read_csv(file, sep=';')


8079962

In [4]:
dict_transport = {1: 'Pas de transport', 
                  2: 'Pied', 
                  3: 'Vélo', 
                  4: 'Deux roues motorisées', 
                  5: 'Voiture, camion, fourgonettes', 
                  6: 'Transport en commun', 
                  }

In [5]:
col_mob = ['COMMUNE', 'DCLT', 'TRANS'] 
df_mob = df_mob_full[col_mob]
df_mob['transport_name'] = df_mob['TRANS'].apply(lambda x: dict_transport.get(x, 'default_value'))
df_mob = df_mob.drop(columns = ['TRANS'])
df_mob = df_mob.rename(columns={'COMMUNE': 'code_commune', 'DCLT': 'code_lieu_travail'})

df_mob["code_commune"] = pd.to_numeric(df_mob["code_commune"], errors="coerce").astype("Int64")
df_mob["code_lieu_travail"] = pd.to_numeric(df_mob["code_lieu_travail"], errors="coerce").astype("Int64")


df_mob.head()

C:\Users\eliot\AppData\Local\Temp\ipykernel_3640\4113551584.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_mob['transport_name'] = df_mob['TRANS'].apply(lambda x: dict_transport.get(x, 'default_value'))


code_commune  code_lieu_travail                 transport_name
0          1001               1001               Pas de transport
1          1001               1001  Voiture, camion, fourgonettes
2          1001               1001               Pas de transport
3          1001               1001               Pas de transport
4          1001               1001  Voiture, camion, fourgonettes

#### La Baule

In [68]:
# On garde uniquement les gens qui viennent d'ailleurs pour travailler à La Baule
code_baule = 44055
df_baule = df_mob[(df_mob['code_lieu_travail'] == code_baule) & (df_mob['code_commune'] != code_baule)]
df_baule

code_commune  code_lieu_travail                 transport_name
535803          13005              44055  Voiture, camion, fourgonettes
986085          19031              44055  Voiture, camion, fourgonettes
986086          19031              44055  Voiture, camion, fourgonettes
2215206         35066              44055  Voiture, camion, fourgonettes
2234447         35143              44055  Voiture, camion, fourgonettes
...               ...                ...                            ...
6473788         85047              44055  Voiture, camion, fourgonettes
6487964         85109              44055  Voiture, camion, fourgonettes
6500972         85163              44055  Voiture, camion, fourgonettes
7120131         92062              44055  Voiture, camion, fourgonettes
7176573         93001              44055               Pas de transport

[1230 rows x 3 columns]

In [ ]:
df_baule_voit = df_baule[df_baule['transport_name'] == 'Voiture, camion, fourgonettes']
df_baule_voit = df_baule_voit.drop(columns = ['transport_name'])
df_baule_voit_unique = df_baule_voit.groupby(["code_commune", "code_lieu_travail"], as_index=False).size()
df_baule_voit_unique = df_baule_voit_unique.rename(columns={'size': 'cnt'})
df_baule_voit_unique['cnt_ev'] = df_baule_voit_unique['cnt'] * ratio_ev
print(df_baule_voit_unique.cnt.sum())

1149


In [72]:
# Loading and preprocessing of communes datasets
gdf_communes_contours = gpd.read_file('../Data/communes-version-simplifiee.geojson')
gdf_communes_contours["code"] = pd.to_numeric(gdf_communes_contours["code"], errors="coerce").astype("Int64")

# Get the centroids of the communes under the metric system, then convert back into angular
gdf_communes_centroids = gdf_communes_contours.to_crs(epsg=2154)
gdf_communes_centroids['centroid'] = gdf_communes_centroids['geometry'].centroid
gdf_communes_centroids = gdf_communes_centroids.drop(columns=['geometry']) 
gdf_communes_centroids['centroid'] = gdf_communes_centroids['centroid'].to_crs(epsg=4326)
gdf_communes_centroids = gdf_communes_centroids.set_geometry('centroid')

gdf_baule_geometry_4326 = gdf_communes_contours[gdf_communes_contours['code'] == 44055].iloc[0]
gdf_baule_centroid = gdf_communes_centroids[gdf_communes_centroids['code'] == 44055]
centroid_baule = gdf_baule_centroid.centroid
coord_centroid_la_baule = [centroid_baule.y, centroid_baule.x]

C:\Users\eliot\AppData\Local\Temp\ipykernel_3640\1114965289.py:14: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  centroid_baule = gdf_baule_centroid.centroid


In [157]:
# Integrate centroids of La Baule and origin city

df_centroid = df_baule_voit_unique.merge(gdf_communes_centroids[['code', 'centroid']], 
              left_on='code_commune', 
              right_on='code', 
              how='left')

# Renommer la colonne pour éviter la confusion
df_centroid.rename(columns={'centroid': 'centroid_hab'}, inplace=True)
df_centroid.drop(columns=['code'], inplace=True)

df_centroid = gpd.GeoDataFrame(df_centroid, geometry="centroid_hab", crs="EPSG:4326")
df_centroid["centroid_lt"] = gpd.GeoSeries([centroid_baule.geometry.iloc[0]] * len(df_centroid), crs="EPSG:4326")

#### People working in La Baule

In [158]:
# Create a base map centered on the mean of all centroids
m = folium.Map(location=coord_centroid_la_baule, zoom_start=8)

# Add all habitation centroids (blue markers)
for _, row in df_centroid.iterrows():
    popup_text = f"Habitation - cnt: {row['cnt']}"
    # folium.Marker([lat_lt, lon_lt],  popup=popup_text, icon=folium.Icon(color="red")).add_to(m)
    color = 'red' if (row['centroid_hab'] == centroid_baule).all() else 'blue' 
    lat_hab, lon_hab = row['centroid_hab'].y, row['centroid_hab'].x
    folium.Marker([lat_hab, lon_hab], popup=popup_text, icon=folium.Icon(color=color)).add_to(m)

# Display the map
m

c:\Users\eliot\anaconda3\Lib\site-packages\folium\utilities.py:101: FutureWarning: Calling float on a single element Series is deprecated and will raise a TypeError in the future. Use float(ser.iloc[0]) instead
  float(coord)
c:\Users\eliot\anaconda3\Lib\site-packages\folium\utilities.py:107: FutureWarning: Calling float on a single element Series is deprecated and will raise a TypeError in the future. Use float(ser.iloc[0]) instead
  if math.isnan(float(coord)):
c:\Users\eliot\anaconda3\Lib\site-packages\folium\utilities.py:109: FutureWarning: Calling float on a single element Series is deprecated and will raise a TypeError in the future. Use float(ser.iloc[0]) instead
  return [float(x) for x in coords]


#### Reducing to a reasonable area 

In [159]:
# buffer_size = 50_000
# buffer_size = 100_000
buffer_size = 150_000
buffer_size_km = buffer_size//1000

area_baule = gdf_baule_centroid.to_crs(epsg=2154)
area_baule["buffer"] = area_baule.geometry.buffer(buffer_size)  # 100 km = 100,000 meters
area_baule = area_baule.set_geometry("buffer").to_crs(epsg=4326)
area_baule.drop(columns=['centroid'], inplace = True)
# area_baule
area_geometry = area_baule.iloc[0].buffer

In [160]:
m = folium.Map(location=coord_centroid_la_baule, zoom_start=7)

# Add all habitation centroids (blue markers)
for _, row in df_centroid.iterrows():
    popup_text = f"Habitation - cnt: {row['cnt']}"
    # folium.Marker([lat_lt, lon_lt],  popup=popup_text, icon=folium.Icon(color="red")).add_to(m)
    color = 'red' if (row['centroid_hab'] == centroid_baule).all() else 'blue' 
    lat_hab, lon_hab = row['centroid_hab'].y, row['centroid_hab'].x
    folium.Marker([lat_hab, lon_hab], popup=popup_text, icon=folium.Icon(color=color)).add_to(m)


geojson = area_baule.to_json()
folium.GeoJson(geojson, name="Buffer", style_function=lambda x: {
    "fillColor": "blue",
    "color": "blue",
    "weight": 2,
    "fillOpacity": 0.2,
}).add_to(m)

# Display the map
m

c:\Users\eliot\anaconda3\Lib\site-packages\folium\utilities.py:101: FutureWarning: Calling float on a single element Series is deprecated and will raise a TypeError in the future. Use float(ser.iloc[0]) instead
  float(coord)
c:\Users\eliot\anaconda3\Lib\site-packages\folium\utilities.py:107: FutureWarning: Calling float on a single element Series is deprecated and will raise a TypeError in the future. Use float(ser.iloc[0]) instead
  if math.isnan(float(coord)):
c:\Users\eliot\anaconda3\Lib\site-packages\folium\utilities.py:109: FutureWarning: Calling float on a single element Series is deprecated and will raise a TypeError in the future. Use float(ser.iloc[0]) instead
  return [float(x) for x in coords]


In [164]:
# Keeping only origins within the area

df_centroid = df_centroid.set_geometry("centroid_hab")
df_centroid['centroid_hab'] = df_centroid['centroid_hab'].to_crs('EPSG:2154')
df_centroid = df_centroid.set_geometry("centroid_lt")
df_centroid['centroid_lt'] = df_centroid['centroid_lt'].to_crs('EPSG:2154')
df_centroid = df_centroid.to_crs('EPSG:2154')

center_point = gdf_baule_centroid.to_crs(epsg=2154)
# Create a 100 km buffer (100,000 meters)
buffer = center_point.buffer(buffer_size).iloc[0]

df_filtered = df_centroid[df_centroid["centroid_hab"].within(buffer)]

df_filtered = df_filtered.to_crs(epsg=4326)
df_filtered["centroid_hab"] = df_filtered["centroid_hab"].to_crs('EPSG:4326')
df_filtered["centroid_lt"] = df_filtered["centroid_lt"].to_crs('EPSG:4326')

df_centroid['centroid_hab'] = df_centroid['centroid_hab'].to_crs('EPSG:4326')
df_centroid['centroid_lt'] = df_centroid['centroid_lt'].to_crs('EPSG:4326')

In [165]:
print(df_filtered.cnt.sum())
print(df_centroid.cnt.sum())
# 50km : 1082/1149 = 94% des trajets 
# 100km : 1133/1149 = 98% des trajets
# 150km : 1139/1149 = 99% des trajets

1139
1149


In [166]:
m = folium.Map(location=coord_centroid_la_baule, zoom_start=8)

# Add all habitation centroids (blue markers)
for _, row in df_filtered.iterrows():
    popup_text = f"Habitation - cnt: {row['cnt']}"
    # folium.Marker([lat_lt, lon_lt],  popup=popup_text, icon=folium.Icon(color="red")).add_to(m)
    color = 'red' if (row['centroid_hab'] == centroid_baule).all() else 'blue' 
    lat_hab, lon_hab = row['centroid_hab'].y, row['centroid_hab'].x
    folium.Marker([lat_hab, lon_hab], popup=popup_text, icon=folium.Icon(color=color)).add_to(m)


geojson = area_baule.to_json()
folium.GeoJson(geojson, name="100 km Buffer", style_function=lambda x: {
    "fillColor": "blue",
    "color": "blue",
    "weight": 2,
    "fillOpacity": 0.2,
}).add_to(m)

# Display the map
m

c:\Users\eliot\anaconda3\Lib\site-packages\folium\utilities.py:101: FutureWarning: Calling float on a single element Series is deprecated and will raise a TypeError in the future. Use float(ser.iloc[0]) instead
  float(coord)
c:\Users\eliot\anaconda3\Lib\site-packages\folium\utilities.py:107: FutureWarning: Calling float on a single element Series is deprecated and will raise a TypeError in the future. Use float(ser.iloc[0]) instead
  if math.isnan(float(coord)):
c:\Users\eliot\anaconda3\Lib\site-packages\folium\utilities.py:109: FutureWarning: Calling float on a single element Series is deprecated and will raise a TypeError in the future. Use float(ser.iloc[0]) instead
  return [float(x) for x in coords]


### Estimer les routes prises pour venir

In [167]:
# Combiner les lignes qui correspondent aux mêmes paires OD
print(len(df_filtered))
df_filtered.head()

92


code_commune  code_lieu_travail  cnt  cnt_ev               centroid_hab  \
2         35066              44055    1   0.046  POINT (-1.70653 48.04524)   
3         35143              44055    1   0.046  POINT (-2.00922 48.24713)   
4         35236              44055    1   0.046  POINT (-2.08122 47.66047)   
5         35238              44055    1   0.046  POINT (-1.68164 48.11158)   
6         35285              44055    1   0.046  POINT (-1.96884 47.76497)   

                 centroid_lt  
2  POINT (-2.35483 47.29059)  
3  POINT (-2.35483 47.29059)  
4  POINT (-2.35483 47.29059)  
5  POINT (-2.35483 47.29059)  
6  POINT (-2.35483 47.29059)

### Get routes and distances

In [168]:
from utils import get_routing
from shapely.geometry import LineString
import time

In [169]:
waiting_time_api = 0.1
df_filtered["routing"] = df_filtered.apply(lambda row: get_routing(row["centroid_hab"].coords[0], row["centroid_lt"].coords[0], delay=waiting_time_api), axis=1)
df_filtered["route"] = df_filtered["routing"].apply(lambda row: LineString(row["geometry"]["coordinates"]))
df_filtered["route"] = gpd.GeoSeries(df_filtered["route"], crs="EPSG:4326")
df_filtered["distance_km"] = df_filtered["routing"].apply(lambda row: row["distance"])
df_filtered.drop(columns=['routing'], inplace=True)
df_filtered = df_filtered.set_geometry('route')
df_filtered.head()

code_commune  code_lieu_travail  cnt  cnt_ev               centroid_hab  \
2         35066              44055    1   0.046  POINT (-1.70653 48.04524)   
3         35143              44055    1   0.046  POINT (-2.00922 48.24713)   
4         35236              44055    1   0.046  POINT (-2.08122 47.66047)   
5         35238              44055    1   0.046  POINT (-1.68164 48.11158)   
6         35285              44055    1   0.046  POINT (-1.96884 47.76497)   

                 centroid_lt  \
2  POINT (-2.35483 47.29059)   
3  POINT (-2.35483 47.29059)   
4  POINT (-2.35483 47.29059)   
5  POINT (-2.35483 47.29059)   
6  POINT (-2.35483 47.29059)   

                                               route  distance_km  
2  LINESTRING (-1.70666 48.04522, -1.70655 48.044...     133.5853  
3  LINESTRING (-2.00612 48.24601, -2.00611 48.246...     161.1485  
4  LINESTRING (-2.083 47.66014, -2.0831 47.66003,...      79.1621  
5  LINESTRING (-1.68136 48.11159, -1.68137 48.111...     133.3113  
6  LINESTRING (-1.96845 47.764, -1.96829 47.76403...      94.1148

In [170]:
# Define the base map, centered on an average location
m = folium.Map(location=coord_centroid_la_baule, zoom_start=8)  # Centered around France

# Ensure your dataframe is a GeoDataFrame
gdf = gpd.GeoDataFrame(df_filtered, geometry="route", crs="EPSG:4326")

# Add each route as a PolyLine on the map
for _, row in gdf.iterrows():
    if isinstance(row["route"], LineString):  # Check if geometry is valid
        folium.PolyLine(
            locations=[(lat, lon) for lon, lat in row["route"].coords],  # Reverse coords for Folium
            color="blue",
            weight=2.5,
            opacity=1
        ).add_to(m)

# Add all workplace centroids (green markers)
for _, row in df_filtered.iterrows():
    # if row['centroid_lt']:
    color='blue'
    lat_1, lon_1 = row['centroid_hab'].y, row['centroid_hab'].x
    lat_2, lon_2 = row['centroid_lt'].y, row['centroid_lt'].x
    folium.Marker([lat_1, lon_1], icon=folium.Icon(color=color)).add_to(m)
    folium.Marker([lat_2, lon_2], icon=folium.Icon(color=color)).add_to(m)

# Display the map
m


c:\Users\eliot\anaconda3\Lib\site-packages\folium\utilities.py:101: FutureWarning: Calling float on a single element Series is deprecated and will raise a TypeError in the future. Use float(ser.iloc[0]) instead
  float(coord)
c:\Users\eliot\anaconda3\Lib\site-packages\folium\utilities.py:107: FutureWarning: Calling float on a single element Series is deprecated and will raise a TypeError in the future. Use float(ser.iloc[0]) instead
  if math.isnan(float(coord)):
c:\Users\eliot\anaconda3\Lib\site-packages\folium\utilities.py:109: FutureWarning: Calling float on a single element Series is deprecated and will raise a TypeError in the future. Use float(ser.iloc[0]) instead
  return [float(x) for x in coords]


### Get the demand for each zone

Idea: cars will recharge their full need in the city if they work or live there. 
* For each pair and zone, 
    * get the intersection with the city + the intersection zone and get the distance ratio
    * attribute to the zone the distance = distance ratio * full distance of the trip
    * multiply by the avg consumption to get the demand 

Problems:
* We consider that people working in La Baule will charge there (and not within their trip before)
* Should we not consider people living in La Baule but rather people living out and working here ? 
* Problem: considering the centroid, people only go through dept. No additional demand in the other zones of the city

In [171]:
gdf_iris_contours = gpd.read_file('../data/IRIS/contours-iris.gpkg')
gdf_iris_contours['code_insee'] = pd.to_numeric(gdf_iris_contours['code_insee'], errors='coerce')
gdf_iris_contours = gdf_iris_contours.dropna(subset=['code_insee'])
gdf_iris_contours['code_insee'] = gdf_iris_contours['code_insee'].astype(int)
gdf_baule_iris = gdf_iris_contours[gdf_iris_contours['code_insee'] ==  44055].to_crs(epsg=4326)

In [172]:
gdf_baule = gdf_communes_contours[gdf_communes_contours['code'] == 44055]
baule_geometry_3395 = gdf_baule.to_crs(epsg=3395).iloc[0]

In [173]:
# S'assurer que les CRS (Systèmes de Référence de Coordonnées) sont compatibles (ici EPSG:4326)
gdf_baule_iris = gdf_baule_iris.to_crs(epsg=3395).reset_index(drop=True)   # Reprojection en CRS projeté (en mètres)
df_filtered = df_filtered.to_crs(epsg=3395)
df_filtered['route'] = df_filtered['route'].to_crs(epsg=3395)
# gdf_baule_geometry = gdf_baule_geometry.to_crs(epsg=3395)

# Calculer la longueur totale des routes interceptées pour chaque quartier
gdf_baule_iris['demand_km'] = 0  # Créer une colonne pour stocker la longueur des routes interceptées

# liste_demand = [0] * len(gdf_baule_iris)
liste_demand_ev = [0] * len(gdf_baule_iris)

for idx, quartier in gdf_baule_iris.iterrows():
    # Initialiser la longueur pour ce quartier
    longueur_total = 0
    longueur_total_ev = 0
    
    # Pour chaque route, calculer l'intersection avec le quartier
    for _, trip in df_filtered.iterrows():
        # Intersecter la route avec le quartier
        intersection_quartier = quartier['geometry'].intersection(trip['route'])
        # intersection_city = gdf_baule_geometry['geometry'].intersection(trip['route'])
        intersection_city = baule_geometry_3395['geometry'].intersection(trip['route'])
        # Temporary fix: mettre iloc[0] mais ça devrait être réglé avec un chgt plus haut
        # intersection_city = gdf_baule_geometry.iloc[0]['geometry'].intersection(trip['route'])

        # Si l'intersection n'est pas vide, ajouter la longueur de l'intersection
        if not intersection_quartier.is_empty:
            # Ajouter la longueur de l'intersection (en km)
            proportion_intercepted_demand = intersection_quartier.length / intersection_city.length
            # longueur_total += (trip['distance_km'] * trip['cnt'] * proportion_intercepted_demand) # déja en km
            longueur_total_ev += (trip['distance_km'] * trip['cnt_ev'] * proportion_intercepted_demand) # déja en km
    
    # liste_demand[idx] = longueur_total
    liste_demand_ev[idx] = longueur_total_ev

# gdf_baule_iris['demand_km'] = liste_demand
gdf_baule_iris['demand_km_ev'] = liste_demand_ev

gdf_baule_iris = gdf_baule_iris.to_crs("EPSG:4326")  # Reprojection en CRS projeté (en mètres)
df_filtered = df_filtered.to_crs("EPSG:4326")
df_filtered['route'] = df_filtered['route'].to_crs(epsg=4326)
gdf_baule_iris['demand_kwh_ev'] = gdf_baule_iris['demand_km_ev'] * conso_kwh_km

## Final plot

In [174]:
import branca
m = folium.Map(location=coord_centroid_la_baule, zoom_start=12)

# Create a colormap based on the number of people in each carreau
min_demand = gdf_baule_iris['demand_kwh_ev'].min()  # Minimum number of people
max_demand = gdf_baule_iris['demand_kwh_ev'].max()  # Maximum number of people
colormap = branca.colormap.linear.YlOrRd_09.scale(min_demand, max_demand)  # Yellow to red color scale

# Add the colormap legend to the map
colormap.add_to(m)

# Ensure your dataframe is a GeoDataFrame
gdf = gpd.GeoDataFrame(df_filtered, geometry="route", crs="EPSG:4326")

# Add each route as a PolyLine on the map
for _, row in gdf.iterrows():
    if isinstance(row["route"], LineString):  # Check if geometry is valid
        folium.PolyLine(
            locations=[(lat, lon) for lon, lat in row["route"].coords],  # Reverse coords for Folium
            color="blue",
            weight=2.5,
            opacity=1
        ).add_to(m)

# Add all workplace centroids (green markers)
for _, row in df_filtered.iterrows():
    color = 'blue'
    lat_1, lon_1 = row['centroid_hab'].y, row['centroid_hab'].x
    
    # Extract the 'cnt' value
    cnt_value = row['cnt']
    
    # Add marker with popup
    folium.Marker(
        [lat_1, lon_1], 
        icon=folium.Icon(color=color), 
        popup=f"Nb voitures (th+ev): {cnt_value}"
    ).add_to(m)

# Iterate through each row in the GeoDataFrame and plot each feature
for _, row in gdf_baule_iris.iterrows():
    # Extract geometry and properties for each feature
    feature = row['geometry']
    demand = row['demand_kwh_ev']  # Assuming this column exists
    nom = row['nom_iris']  # Assuming this column exists

    # Create a popup displaying the number of people
    text = f"{nom} : Additional demand={demand:.2f}kWh"
    popup = folium.Popup(text, max_width=300)
    
    # Style each feature based on the number of people
    folium.GeoJson(
        feature,
        name=f"Carreau {row.name}",
        popup=popup,
        style_function=lambda x, demand=demand: {
                'fillColor': colormap(demand),  # Color based on the number of people
                'color': 'black',  # Border color
                'weight': 2,  # Border width
                'fillOpacity': 0.7  # Fill opacity
            }
    ).add_to(m)
    
# Ajouter un contrôle des couches
folium.LayerControl().add_to(m)

# Afficher la carte
m

c:\Users\eliot\anaconda3\Lib\site-packages\folium\utilities.py:101: FutureWarning: Calling float on a single element Series is deprecated and will raise a TypeError in the future. Use float(ser.iloc[0]) instead
  float(coord)
c:\Users\eliot\anaconda3\Lib\site-packages\folium\utilities.py:107: FutureWarning: Calling float on a single element Series is deprecated and will raise a TypeError in the future. Use float(ser.iloc[0]) instead
  if math.isnan(float(coord)):
c:\Users\eliot\anaconda3\Lib\site-packages\folium\utilities.py:109: FutureWarning: Calling float on a single element Series is deprecated and will raise a TypeError in the future. Use float(ser.iloc[0]) instead
  return [float(x) for x in coords]


In [177]:
import branca
m = folium.Map(location=coord_centroid_la_baule, zoom_start=12)

# Create a colormap based on the number of people in each carreau
min_demand = gdf_baule_iris['demand_kwh_ev'].min()  # Minimum number of people
max_demand = gdf_baule_iris['demand_kwh_ev'].max()  # Maximum number of people
colormap = branca.colormap.linear.YlOrRd_09.scale(min_demand, max_demand)  # Yellow to red color scale

# Add the colormap legend to the map
colormap.add_to(m)


# Iterate through each row in the GeoDataFrame and plot each feature
for _, row in gdf_baule_iris.iterrows():
    # Extract geometry and properties for each feature
    feature = row['geometry']
    demand = row['demand_kwh_ev']  # Assuming this column exists
    nom = row['nom_iris']  # Assuming this column exists

    # Create a popup displaying the number of people
    text = f"{nom} : Additional demand={demand:.2f}kWh"
    popup = folium.Popup(text, max_width=300)
    
    # Style each feature based on the number of people
    folium.GeoJson(
        feature,
        name=f"Carreau {row.name}",
        popup=popup,
        style_function=lambda x, demand=demand: {
                'fillColor': colormap(demand),  # Color based on the number of people
                'color': 'black',  # Border color
                'weight': 2,  # Border width
                'fillOpacity': 0.7  # Fill opacity
            }
    ).add_to(m)
    
# Ajouter un contrôle des couches
folium.LayerControl().add_to(m)

# Afficher la carte
m

c:\Users\eliot\anaconda3\Lib\site-packages\folium\utilities.py:101: FutureWarning: Calling float on a single element Series is deprecated and will raise a TypeError in the future. Use float(ser.iloc[0]) instead
  float(coord)
c:\Users\eliot\anaconda3\Lib\site-packages\folium\utilities.py:107: FutureWarning: Calling float on a single element Series is deprecated and will raise a TypeError in the future. Use float(ser.iloc[0]) instead
  if math.isnan(float(coord)):
c:\Users\eliot\anaconda3\Lib\site-packages\folium\utilities.py:109: FutureWarning: Calling float on a single element Series is deprecated and will raise a TypeError in the future. Use float(ser.iloc[0]) instead
  return [float(x) for x in coords]


In [175]:
gdf_baule_iris.to_file(f"../data/RP2020_MOBPRO_csv/demand_per_iris_{buffer_size_km}km.geojson", driver="GeoJSON")

# ToDO

* Faire des fonctions pour automatiser le code
* Faire un NB avec uniquement le nécessaire sans remarque etc (input => output)